# Audio Nearest Neighbors

## Imports

In [2]:
import os
import numpy as np
import librosa
import torch
import torchaudio
import audio_analysis
from matplotlib import pyplot as plt
import wave
import time

import IPython
from IPython.display import display
import ipywidgets as widgets

In [2]:
## Audio Settings

In [3]:
audio_file_path = "../../Data/sounds/Night_and_Day_by_Virginia_Woolf_48khz.wav"
audio_sample_rate = 48000
audio_channel_count = 1
audio_range_sec = [ 10.0, 70.0 ]
audio_excerpt_length = 1.0 # in secs
audio_excerpt_offset = 0.5 # in secs

audio_feature_names = ["root mean square", "mfcc"]

audio_audio_file_path_gui = widgets.Text(value=audio_file_path, description="Audio File Path:", style={'description_width': 'initial'}) 
audio_sample_rate_gui = widgets.IntText(value=audio_sample_rate, description="Audio Sample Rate:", style={'description_width': 'initial'})
audio_channel_count_gui = widgets.IntText(value=audio_channel_count, description="Audio Channel Count:", style={'description_width': 'initial'})
audio_range_sec_gui_1 = widgets.FloatText(value=audio_range_sec[0], description="Audio Range Start (secs):", style={'description_width': 'initial'})
audio_range_sec_gui_2 = widgets.FloatText(value=audio_range_sec[1], description="Audio Range End (secs):", style={'description_width': 'initial'})
audio_excerpt_length_gui = widgets.FloatText(value=audio_excerpt_length, description="Audio Excerpt Length (secs):", style={'description_width': 'initial'})
audio_excerpt_offset_gui = widgets.FloatText(value=audio_excerpt_offset, description="Audio Excerpt Offset (secs):", style={'description_width': 'initial'})

audio_feature_names_gui = widgets.SelectMultiple(
    options=[ "root mean square",  "chroma stft", "chroma cqt", "chroma cens", "chroma vqt", "mel spectrogram", 
"mfcc", "spectral centroid", "spectral bandwidth", "spectral contrast", "spectral flatness", "spectral rolloff", "tempo", "tempogram", "tempogram ratio" ],
    value=["root mean square"],
    description='Audio Features',
    disabled=False,
    style={'description_width': 'initial'}
)

display(audio_audio_file_path_gui)
display(audio_sample_rate_gui)
display(audio_channel_count_gui)
display(audio_range_sec_gui_1)
display(audio_range_sec_gui_2)
display(audio_excerpt_length_gui)
display(audio_excerpt_offset_gui)
display(audio_feature_names_gui)

Text(value='../../Data/sounds/Night_and_Day_by_Virginia_Woolf_48khz.wav', description='Audio File Path:', styl…

IntText(value=48000, description='Audio Sample Rate:', style=DescriptionStyle(description_width='initial'))

IntText(value=1, description='Audio Channel Count:', style=DescriptionStyle(description_width='initial'))

FloatText(value=10.0, description='Audio Range Start (secs):', style=DescriptionStyle(description_width='initi…

FloatText(value=70.0, description='Audio Range End (secs):', style=DescriptionStyle(description_width='initial…

FloatText(value=1.0, description='Audio Excerpt Length (secs):', style=DescriptionStyle(description_width='ini…

FloatText(value=0.5, description='Audio Excerpt Offset (secs):', style=DescriptionStyle(description_width='ini…

SelectMultiple(description='Audio Features', index=(0,), options=('root mean square', 'chroma stft', 'chroma c…

In [4]:
audio_file_path = audio_audio_file_path_gui.value
audio_sample_rate = audio_sample_rate_gui.value
audio_channel_count = audio_channel_count_gui.value
audio_range_sec[0] = audio_range_sec_gui_1.value
audio_range_sec[1] = audio_range_sec_gui_2.value
audio_excerpt_length = audio_excerpt_length_gui.value
audio_excerpt_offset = audio_excerpt_offset_gui.value
audio_feature_names = list(audio_feature_names_gui.value)

## Load Audio

In [5]:
audio_waveform, _ = librosa.load(audio_file_path, sr=audio_sample_rate)

if audio_channel_count > 1:
    audio_waveform = audio_waveform[0]

audio_waveform = audio_waveform[int(audio_range_sec[0] * audio_sample_rate):int(audio_range_sec[1] * audio_sample_rate)]
audio_waveform_sc = audio_waveform.shape[0]

## Create Audio Excerpts

In [6]:
audio_excerpts = []

audio_excerpt_length_sc = int(audio_excerpt_length * audio_sample_rate)
audio_excerpt_offset_sc = int(audio_excerpt_offset * audio_sample_rate)

for sI in range(0, audio_waveform_sc - audio_excerpt_length_sc, audio_excerpt_offset_sc):
    
    audio_excerpt = audio_waveform[sI:sI + audio_excerpt_length_sc]
    audio_excerpts.append(audio_excerpt)
    
audio_waveforms = np.stack(audio_excerpts, axis=0)

In [22]:
audio_sample_overlap

24000

## Calculate Audio Features

In [7]:
audio_features = {}

audio_features["waveform"] = audio_waveforms
if "root mean square" in audio_feature_names:
    audio_features["root mean square"] = audio_analysis.rms(audio_waveforms)
if "chroma stft" in audio_feature_names:
    audio_features["chroma stft"] = audio_analysis.chroma_stft(audio_waveforms, audio_sample_rate)
if "chroma cqt" in audio_feature_names:
    audio_features["chroma cqt"] = audio_analysis.chroma_cqt(audio_waveforms, audio_sample_rate)
if "chroma cens" in audio_feature_names:
    audio_features["chroma cens"] = audio_analysis.chroma_cens(audio_waveforms, audio_sample_rate)
if "chroma vqt" in audio_feature_names:
    audio_features["chroma vqt"] = audio_analysis.chroma_vqt(audio_waveforms, audio_sample_rate)
if "mel spectrogram" in audio_feature_names:
    audio_features["mel spectrogram"] = audio_analysis.mel_spectrogram(audio_waveforms, audio_sample_rate)
if "mfcc" in audio_feature_names:
    audio_features["mfcc"] = audio_analysis.mfcc(audio_waveforms, audio_sample_rate)
if "spectral centroid" in audio_feature_names:
    audio_features["spectral centroid"] = audio_analysis.spectral_centroid(audio_waveforms, audio_sample_rate)
if "spectral bandwidth" in audio_feature_names:
    audio_features["spectral bandwidth"] = audio_analysis.spectral_bandwidth(audio_waveforms, audio_sample_rate)
if "spectral contrast" in audio_feature_names:
    audio_features["spectral contrast"] = audio_analysis.spectral_contrast(audio_waveforms, audio_sample_rate)
if "spectral flatness" in audio_feature_names:
    audio_features["spectral flatness"] = audio_analysis.spectral_flatness(audio_waveforms)
if "spectral rolloff" in audio_feature_names:
    audio_features["spectral rolloff"] = audio_analysis.spectral_rolloff(audio_waveforms, audio_sample_rate)
if "tempo" in audio_feature_names:
    audio_features["tempo"] = audio_analysis.tempo(audio_waveforms, audio_sample_rate)
if "tempogram" in audio_feature_names:
    audio_features["tempogram"] = audio_analysis.tempogram(audio_waveforms, audio_sample_rate)
if "tempogram ratio" in audio_feature_names:
    audio_features["tempogram ratio"] = audio_analysis.tempogram_ratio(audio_waveforms, audio_sample_rate)

## Normalise Audio Features

In [8]:
for audio_feature_name in list(audio_features.keys()):
    
    #print(audio_feature_name)
    
    audio_feature = audio_features[audio_feature_name]
    
    audio_feature_mean = np.mean(audio_feature)
    audio_feature_std = np.std(audio_feature)
    
    audio_feature_norm = (audio_feature - audio_feature_mean) / audio_feature_std
    
    #print("audio_feature_norm s ", audio_feature_norm.shape)

    audio_features[audio_feature_name + " norm"] = audio_feature_norm

## Find Nearest Neighbors

In [9]:
# gather all waveforms and audio features
audio_features_proc = []
for audio_feature_name in audio_feature_names:
    audio_norm_feature_name = audio_feature_name + " norm"
    audio_feature = audio_features[audio_norm_feature_name]
    #print("name ", audio_norm_feature_name, " shape ", audio_feature.shape)
    audio_features_proc.append(audio_feature)
    
audio_features_proc = np.concatenate(audio_features_proc, axis=1)
audio_waveforms_proc = np.copy(audio_waveforms)

# select first audio feature to begin search with
nn_current_index = 0
nn_current_waveform = audio_waveforms_proc[nn_current_index]
nn_current_feature = audio_features_proc[nn_current_index]
nn_current_feature = np.expand_dims(nn_current_feature, 0)

# prepare empty waveform to copy waveforms corresponding to nearest features into
nn_element_count = audio_features_proc.shape[0]
gen_waveform_sample_count = 2 * audio_excerpt_length_sc + (nn_element_count - 1) * audio_excerpt_offset_sc
gen_waveform = np.zeros(gen_waveform_sample_count)

# create amplitude enevelope for blending audio waveforms into gen_waveform
audio_sample_overlap = audio_excerpt_length_sc - audio_excerpt_offset_sc
hann_window = torch.hann_window(audio_sample_overlap * 2).numpy()

amplitude_envelope = np.ones([audio_excerpt_length_sc])
amplitude_envelope[:audio_sample_overlap] *= hann_window[:audio_sample_overlap]
amplitude_envelope[-audio_sample_overlap:] *= hann_window[audio_sample_overlap:]

# add first waveform to gen waveform
gen_waveform[:audio_excerpt_length_sc] += nn_current_waveform * amplitude_envelope

# iterate through all neighbors
sI = audio_excerpt_length_sc -  audio_sample_overlap # sample index for waveform insertion in gen waveform

remaining_neighbor_gui = widgets.Label(value=str(nn_element_count))

display(remaining_neighbor_gui)

while nn_element_count > 0:

    remaining_neighbor_gui.value = str(nn_element_count)

    # search nearest element
    nn_distances = np.linalg.norm(audio_features_proc - nn_current_feature, axis=1)
    k = 2
    nn_indices = nn_distances.argsort()[:k]

    # replace current element with nearest element
    nn_previous_index = nn_current_index
    nn_current_index = nn_indices[1]
    nn_current_waveform = audio_waveforms_proc[nn_current_index]
    nn_current_feature = audio_features_proc[nn_current_index]
    nn_current_feature = np.expand_dims(nn_current_feature, 0)
    
    # blend waveform corresponding to current element into gen waveform
    gen_waveform[sI:sI + audio_excerpt_length_sc] += nn_current_waveform * amplitude_envelope
    
    # remove previous element
    if nn_previous_index == 0:
        audio_waveforms_proc = np.copy(audio_waveforms_proc[nn_previous_index + 1:])
        audio_features_proc = np.copy(audio_features_proc[nn_previous_index + 1:])
    elif nn_previous_index == audio_waveforms_proc.shape[0] - 1:
        audio_waveforms_proc = np.copy(audio_waveforms_proc[:nn_previous_index])
        audio_features_proc = np.copy(audio_features_proc[:nn_previous_index])
    else:
        audio_waveforms_proc = np.copy(np.concatenate([audio_waveforms_proc[:nn_previous_index], audio_waveforms_proc[nn_previous_index + 1:]], axis=0))
        audio_features_proc = np.copy(np.concatenate([audio_features_proc[:nn_previous_index], audio_features_proc[nn_previous_index + 1:]], axis=0))

    nn_element_count -= 1
    sI += audio_excerpt_length_sc - audio_sample_overlap

Label(value='66')

## Play Generated Waveform

In [10]:
IPython.display.Audio(gen_waveform,rate=audio_sample_rate)

## Save Generated Waveform

In [11]:
gen_waveform = torch.tensor(gen_waveform)
gen_waveform = gen_waveform.unsqueeze(0)
torchaudio.save("data_proc/gen_waveform.wav", gen_waveform, audio_sample_rate)